The purpose of this notebook is a quick demonstration of the joblibspark library, how it can be used to distribute training jobs in parallel. It considers two models, the sklearn RandomForestClassifier, and the CatboostClassifier. It compares the train time on a GridSearch using a single core, using multiple cores, and using multiple cores under a Spark parallel backend.

The conclusion is that the benfit of parallelism is dependent on the model being trained and actually having access to a cluster. For RandomForestClassifier, which is single threaded by default, significant improvements are seen in parallelism. Also note that n_jobs was set to 8 (on a 16 core machine). Additionally, using the Spark backend incurs signficant overhead compared to the native joblib backend, which means the Spark backend will not be useful on a single machine and will only be useful when your training size and model of choice allows you to distribute over several machines.

Although not directly related to Spark distribution, it is worth noting here that some algorithms already use multithreading. This should be a consideration for how those are distributed, as having too many run on a single machine will not be helpful. Notice that Catboost models only have n_jobs of 2, since that fully maximizes the utilization of the cores 

In [14]:
import pandas as pd
import numpy as np

from sklearn.utils import parallel_backend

from catboost import CatBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split, GridSearchCV

from joblibspark import register_spark


In [15]:
data = pd.read_csv('./dataset.csv')

In [16]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9709 entries, 0 to 9708
Data columns (total 20 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ID               9709 non-null   int64  
 1   Gender           9709 non-null   int64  
 2   Own_car          9709 non-null   int64  
 3   Own_property     9709 non-null   int64  
 4   Work_phone       9709 non-null   int64  
 5   Phone            9709 non-null   int64  
 6   Email            9709 non-null   int64  
 7   Unemployed       9709 non-null   int64  
 8   Num_children     9709 non-null   int64  
 9   Num_family       9709 non-null   int64  
 10  Account_length   9709 non-null   int64  
 11  Total_income     9709 non-null   float64
 12  Age              9709 non-null   float64
 13  Years_employed   9709 non-null   float64
 14  Income_type      9709 non-null   object 
 15  Education_type   9709 non-null   object 
 16  Family_status    9709 non-null   object 
 17  Housing_type  

Just a quick demonstration of the the relative speed of different optimization methods. Accuracy is not the end goal.

In [17]:
X = pd.get_dummies(data.drop('Target', axis=1))
y = data['Target']

In [18]:
rf = RandomForestClassifier()

param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [10,15,20],
    'min_samples_split': [2, 5, 10]
}

In [19]:
rf_cv_single_core = GridSearchCV(rf, param_grid, cv=5, n_jobs=1)

rf_cv_single_core.fit(X, y)

GridSearchCV(cv=5, estimator=RandomForestClassifier(), n_jobs=1,
             param_grid={'max_depth': [10, 15, 20],
                         'min_samples_split': [2, 5, 10],
                         'n_estimators': [100, 200, 300]})

In [20]:
rf_cv_multi_core = GridSearchCV(rf, param_grid, cv=5, n_jobs=8)

rf_cv_multi_core.fit(X, y)

GridSearchCV(cv=5, estimator=RandomForestClassifier(), n_jobs=8,
             param_grid={'max_depth': [10, 15, 20],
                         'min_samples_split': [2, 5, 10],
                         'n_estimators': [100, 200, 300]})

In [21]:
register_spark()

with parallel_backend('spark', n_jobs=8):
    rf_cv_spark = GridSearchCV(rf, param_grid, cv=5)

    rf_cv_spark.fit(X, y)

In [22]:
X = data.drop('Target', axis=1)
y = data['Target']

In [23]:
cat = CatBoostClassifier(cat_features=['Income_type','Education_type','Family_status','Housing_type','Occupation_type'])

params = {
    'iterations': [100, 200, 300],
    'learning_rate': [0.01, 0.05, 0.1, 0.5],
    'depth': [3, 5, 7],

}

In [24]:
cat_cv_single_core = GridSearchCV(cat, params, cv=5, n_jobs=1)

cat_cv_single_core.fit(X, y)

0:	learn: 0.6877794	total: 1.04ms	remaining: 103ms
1:	learn: 0.6825342	total: 1.98ms	remaining: 96.9ms
2:	learn: 0.6773969	total: 2.8ms	remaining: 90.5ms
3:	learn: 0.6723249	total: 3.49ms	remaining: 83.8ms
4:	learn: 0.6673534	total: 4.17ms	remaining: 79.2ms
5:	learn: 0.6624972	total: 4.82ms	remaining: 75.5ms
6:	learn: 0.6577478	total: 5.49ms	remaining: 73ms
7:	learn: 0.6530739	total: 6.16ms	remaining: 70.8ms
8:	learn: 0.6485097	total: 6.76ms	remaining: 68.3ms
9:	learn: 0.6440225	total: 7.42ms	remaining: 66.8ms
10:	learn: 0.6396309	total: 8.05ms	remaining: 65.1ms
11:	learn: 0.6352921	total: 8.8ms	remaining: 64.5ms
12:	learn: 0.6310689	total: 9.47ms	remaining: 63.4ms
13:	learn: 0.6269020	total: 10.2ms	remaining: 62.4ms
14:	learn: 0.6228208	total: 10.8ms	remaining: 61ms
15:	learn: 0.6188253	total: 11.4ms	remaining: 59.8ms
16:	learn: 0.6148873	total: 12ms	remaining: 58.8ms
17:	learn: 0.6109855	total: 12.7ms	remaining: 57.7ms
18:	learn: 0.6071775	total: 13.4ms	remaining: 57.2ms
19:	learn: 0

GridSearchCV(cv=5,
             estimator=<catboost.core.CatBoostClassifier object at 0x7f7d327168c0>,
             n_jobs=1,
             param_grid={'depth': [3, 5, 7], 'iterations': [100, 200, 300],
                         'learning_rate': [0.01, 0.05, 0.1, 0.5]})

In [25]:
cat_cv_multi_core = GridSearchCV(cat, params, cv=5, n_jobs=2)

cat_cv_multi_core.fit(X, y)

0:	learn: 0.6877794	total: 53.6ms	remaining: 5.31s
1:	learn: 0.6825342	total: 58.3ms	remaining: 2.85s
2:	learn: 0.6773969	total: 65.1ms	remaining: 2.1s
0:	learn: 0.6877795	total: 60.6ms	remaining: 6s
3:	learn: 0.6723249	total: 70.5ms	remaining: 1.69s
1:	learn: 0.6825368	total: 66.3ms	remaining: 3.25s
4:	learn: 0.6673534	total: 77.3ms	remaining: 1.47s
2:	learn: 0.6773983	total: 71.9ms	remaining: 2.32s
3:	learn: 0.6723295	total: 75.6ms	remaining: 1.81s
5:	learn: 0.6624972	total: 83ms	remaining: 1.3s
4:	learn: 0.6673636	total: 79.5ms	remaining: 1.51s
6:	learn: 0.6577478	total: 86.9ms	remaining: 1.15s
5:	learn: 0.6625117	total: 83.2ms	remaining: 1.3s
7:	learn: 0.6530739	total: 90.8ms	remaining: 1.04s
6:	learn: 0.6577611	total: 86.3ms	remaining: 1.15s
7:	learn: 0.6530912	total: 89ms	remaining: 1.02s
8:	learn: 0.6485097	total: 97.4ms	remaining: 985ms
8:	learn: 0.6485299	total: 91ms	remaining: 921ms
9:	learn: 0.6440426	total: 94ms	remaining: 846ms
9:	learn: 0.6440225	total: 102ms	remaining: 9

GridSearchCV(cv=5,
             estimator=<catboost.core.CatBoostClassifier object at 0x7f7d327168c0>,
             n_jobs=2,
             param_grid={'depth': [3, 5, 7], 'iterations': [100, 200, 300],
                         'learning_rate': [0.01, 0.05, 0.1, 0.5]})

In [26]:
register_spark()

with parallel_backend('spark', n_jobs=2):
    cat_cv_spark = GridSearchCV(cat, params, cv=5)

    cat_cv_spark.fit(X, y)

0:	learn: 0.6877794	total: 53.7ms	remaining: 5.32s
1:	learn: 0.6825342	total: 58.2ms	remaining: 2.85s
2:	learn: 0.6773969	total: 63.6ms	remaining: 2.06s
3:	learn: 0.6723249	total: 67ms	remaining: 1.61s
0:	learn: 0.6877795	total: 58ms	remaining: 5.74s
4:	learn: 0.6673534	total: 71.6ms	remaining: 1.36s
1:	learn: 0.6825368	total: 62.6ms	remaining: 3.07s
5:	learn: 0.6624972	total: 75.2ms	remaining: 1.18s
2:	learn: 0.6773983	total: 67.8ms	remaining: 2.19s
6:	learn: 0.6577478	total: 78.5ms	remaining: 1.04s
7:	learn: 0.6530739	total: 82.3ms	remaining: 946ms
3:	learn: 0.6723295	total: 72.9ms	remaining: 1.75s
8:	learn: 0.6485097	total: 86.2ms	remaining: 872ms
4:	learn: 0.6673636	total: 76.8ms	remaining: 1.46s
9:	learn: 0.6440225	total: 89.9ms	remaining: 809ms
5:	learn: 0.6625117	total: 80.4ms	remaining: 1.26s
10:	learn: 0.6396309	total: 93.7ms	remaining: 758ms
6:	learn: 0.6577611	total: 85.1ms	remaining: 1.13s
11:	learn: 0.6352921	total: 98ms	remaining: 719ms
7:	learn: 0.6530912	total: 89ms	rem

0:	learn: 0.6877975	total: 1.25ms	remaining: 124ms
1:	learn: 0.6825402	total: 2.49ms	remaining: 122ms
2:	learn: 0.6773844	total: 3.26ms	remaining: 106ms
3:	learn: 0.6723492	total: 4.03ms	remaining: 96.7ms
4:	learn: 0.6673899	total: 5ms	remaining: 95ms
5:	learn: 0.6625453	total: 5.73ms	remaining: 89.7ms
6:	learn: 0.6578021	total: 6.47ms	remaining: 86ms
7:	learn: 0.6531318	total: 7.35ms	remaining: 84.6ms
8:	learn: 0.6485525	total: 8.19ms	remaining: 82.8ms
9:	learn: 0.6440582	total: 8.98ms	remaining: 80.9ms
10:	learn: 0.6396351	total: 9.79ms	remaining: 79.2ms
11:	learn: 0.6352870	total: 10.6ms	remaining: 77.8ms
12:	learn: 0.6310301	total: 11.4ms	remaining: 76.3ms
13:	learn: 0.6268546	total: 12.2ms	remaining: 74.9ms
14:	learn: 0.6227658	total: 13ms	remaining: 73.8ms
15:	learn: 0.6187588	total: 13.8ms	remaining: 72.5ms
16:	learn: 0.6148225	total: 14.5ms	remaining: 70.9ms
17:	learn: 0.6109669	total: 15.2ms	remaining: 69.5ms
18:	learn: 0.6071644	total: 16ms	remaining: 68.2ms
19:	learn: 0.6034